<a href="https://colab.research.google.com/github/minhtranc1991/quantitative_trading_analyst_py/blob/main/VWAP.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
!pip install --upgrade binance-historical-data plotly -q

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 9.6/9.6 MB 39.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 272.8/272.8 kB 16.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.6/1.6 MB 27.6 MB/s eta 0:00:00


In [ ]:
import os
import warnings
import numpy as np
import pandas as pd
import plotly.graph_objects as go
from tqdm.notebook import tqdm
from plotly.subplots import make_subplots
from datetime import datetime, timedelta, date, time
from binance_historical_data import BinanceDataDumper
warnings.filterwarnings('ignore')

In [ ]:
def get_list_all_trading_pairs():
    data_dumper = BinanceDataDumper(
        path_dir_where_to_dump=".",
        asset_class="spot",
        data_type="klines",
        data_frequency="1h",
    )
    return data_dumper.get_list_all_trading_pairs()

def filter_usdt_tickers(tickers):
    exclude_keywords = ["UPUSDT", "DOWNUSDT", "BEARUSDT", "BULLUSDT"]
    return [ticker for ticker in tickers if ticker.endswith("USDT") and not any(ex in ticker for ex in exclude_keywords)]

def find_first_data_date(ticker):
    data_dumper = BinanceDataDumper(
        path_dir_where_to_dump=".",
        asset_class="spot",
        data_type="klines",
        data_frequency="1h",
    )
    return data_dumper.get_min_start_date_for_ticker(ticker)

def format_time(seconds):
    hours = int(seconds // 3600)
    minutes = int((seconds % 3600) // 60)
    secs = int(seconds % 60)
    return f"{hours:02d}:{minutes:02d}:{secs:02d}"

def detect_timestamp_unit(timestamp):
    num_digits = len(str(timestamp))
    if num_digits == 13:
        return 'ms'
    elif num_digits == 16:
        return 'us'
    else:
        raise ValueError(f"Timestamp không hợp lệ: {timestamp}")

def convert_timestamp(timestamp):
    unit = detect_timestamp_unit(timestamp)
    return pd.to_datetime(timestamp, unit=unit, errors='coerce')

def download_ticker(ticker, date_start, date_end, data_frequency="1h"):
    data_dumper = BinanceDataDumper(
        path_dir_where_to_dump=".",
        asset_class="spot",
        data_type="klines",
        data_frequency= data_frequency,
    )
    date_start = datetime.strptime(date_start, "%Y-%m-%d").date()
    date_end = datetime.strptime(date_end, "%Y-%m-%d").date()
    data_dumper.dump_data(
        tickers = ticker,
        date_start = date_start,
        date_end = date_end,
        is_to_update_existing = False,
    )

def read_csv_file(file_path):
    df = pd.read_csv(file_path)
    df.columns = [
        "open_time", "Open", "High", "Low", "Close", "volume",
        "close_time", "quote_asset_volume", "number_of_trades",
        "taker_buy_base_asset_volume", "taker_buy_quote_asset_volume", "ignore"
    ]
    df['open_time'] = df['open_time'].apply(convert_timestamp)
    df['close_time'] = df['close_time'].apply(convert_timestamp)
    return df

def get_csv_files(directory):
    try:
        if not os.path.exists(directory):
            print(f"Warning: Thư mục không tồn tại: {directory}")
            return []
        return [os.path.join(directory, f) for f in os.listdir(directory) if f.endswith('.csv')]
    except Exception as e:
        print(f"Lỗi khi đọc thư mục {directory}: {str(e)}")
        return []

# Load data from file
def process_csv_files(ticker, data_frequency = "1h"):
    daily_path = os.path.join(os.getcwd(), f"spot/daily/klines/{ticker}/{data_frequency}")
    monthly_path = os.path.join(os.getcwd(), f"spot/monthly/klines/{ticker}/{data_frequency}")
    daily_files = get_csv_files(daily_path)
    monthly_files = get_csv_files(monthly_path)
    all_files = daily_files + monthly_files
    if not all_files:
        print(f"❗ Không có file CSV nào cho {ticker}")
        return None
    data = pd.concat([read_csv_file(file) for file in all_files], ignore_index=True)
    data.sort_values(by='open_time', inplace=True)
    return data

In [ ]:
ticker = 'BTCUSDT'
data_frequency = '5m'
end_date = date.today() - timedelta(days=1)
start_date = end_date - timedelta(days=30)
end_date = end_date.strftime("%Y-%m-%d")
start_date = start_date.strftime("%Y-%m-%d")

download_ticker(ticker, start_date, end_date, data_frequency)
data = process_csv_files(ticker, data_frequency)
data = data.drop(columns=['close_time',	'quote_asset_volume',	'number_of_trades',	'taker_buy_base_asset_volume',	'taker_buy_quote_asset_volume',	'ignore'])
data


---> Found overall tickers: 588
---> Filter to asked tickers: 7
------> Tickers left: 2
Download full data for 2 tickers: 
---> Data will be saved here: /content/spot
---> Data Frequency: 5m
---> Start Date: 20250620
---> End Date: 20250720


Tickers:   0%|          | 0/2 [00:00<?, ?it/s]

monthly files to download:   0%|          | 0/1 [00:00<?, ?files/s]

daily files to download:   0%|          | 0/20 [00:00<?, ?files/s]

monthly files to download: 0files [00:00, ?files/s]

daily files to download:   0%|          | 0/20 [00:00<?, ?files/s]

Tried to dump data for 2 tickers:
---> For BTCUSDT new data saved for: 1 months 15 days
---> For BTCUSD new data saved for: 0 months 0 days


open_time       Open       High        Low      Close    volume
4305 2025-06-01 00:05:00  104530.43  104559.56  104509.21  104535.84  22.60329
4306 2025-06-01 00:10:00  104535.84  104536.59  104454.41  104473.01  24.19999
4307 2025-06-01 00:15:00  104473.01  104487.81  104396.22  104462.18  42.12392
4308 2025-06-01 00:20:00  104462.17  104490.57  104374.79  104433.71  22.53878
4309 2025-06-01 00:25:00  104433.70  104457.71  104370.26  104380.96  30.94389
...                  ...        ...        ...        ...        ...       ...
4013 2025-07-15 23:35:00  117500.01  117643.71  117500.00  117639.99  29.86757
4014 2025-07-15 23:40:00  117640.00  117784.65  117638.74  117784.65  25.58673
4015 2025-07-15 23:45:00  117784.64  117784.65  117695.87  117707.08  29.95267
4016 2025-07-15 23:50:00  117707.08  117714.63  117630.00  117714.63  18.59052
4017 2025-07-15 23:55:00  117714.62  117794.02  117706.80  117758.09  14.55459

[12944 rows x 6 columns]

In [ ]:
def get_periods_per_year(freq: str) -> int:
    if freq.endswith('m'):  # phút
        minutes = int(freq[:-1])
        return int(365 * 24 * 60 / minutes)
    elif freq.endswith('h'):  # giờ
        hours = int(freq[:-1])
        return int(365 * 24 / hours)
    elif freq.endswith('d'):  # ngày
        return 365
    elif freq.endswith('w'):  # tuần
        return 52
    else:
        raise ValueError(f"Không hỗ trợ định dạng data_frequency: {freq}")

def calculate_sharpe_ratio(returns_series: pd.Series, data_frequency: str, annualized_risk_free_rate: float = 0.03) -> float:
    """
    Tính toán Sharpe Ratio hàng năm từ một chuỗi lợi nhuận theo kỳ.

    Args:
        returns_series (pd.Series): Chuỗi lợi nhuận của chiến lược theo từng kỳ.
        data_frequency (str): Tần suất của dữ liệu ('15m', '1H', '1D').
        annualized_risk_free_rate (float): Lãi suất phi rủi ro hàng năm.

    Returns:
        float: Giá trị Sharpe Ratio đã được quy đổi ra năm.
    """
    # Xử lý trường hợp không có giao dịch hoặc không có biến động
    if returns_series.std() == 0 or pd.isna(returns_series.std()):
        return 0.0

    # 1. Lấy số kỳ trong một năm
    periods_per_year = get_periods_per_year(data_frequency)

    # 2. Quy đổi lãi suất phi rủi ro ra theo từng kỳ
    rf_per_period = annualized_risk_free_rate / periods_per_year

    # 3. Tính toán Sharpe Ratio
    # Lợi nhuận trung bình mỗi kỳ trừ đi lãi suất phi rủi ro mỗi kỳ
    excess_return_mean = returns_series.mean() - rf_per_period

    # Sharpe Ratio hàng ngày = Lợi nhuận vượt trội trung bình / Độ lệch chuẩn lợi nhuận
    sharpe_ratio = excess_return_mean / returns_series.std()

    # 4. Quy đổi ra Sharpe Ratio hàng năm
    annualized_sharpe = sharpe_ratio * np.sqrt(periods_per_year)

    return annualized_sharpe

def backtest_vwap(df, a, b,
                                 fee_rate=0.0005,
                                 slippage_range=(0.001, 0.005),
                                 spread_range=(0.001, 0.005)
                                ):
    """
    Thực hiện backtest chiến lược GIAO CẮT (Crossover) Rolling VWAP (MVWAP).
    Đây là chiến lược Long/Short, có tính đến các chi phí thực tế ngẫu nhiên.

    Args:
        df (pd.DataFrame): DataFrame dữ liệu.
        a (int): Cửa sổ của MVWAP nhanh.
        b (int): Cửa sổ của MVWAP chậm.
        fee_rate (float): Tỷ lệ phí giao dịch cố định.
        slippage_range (tuple): Khoảng (min, max) cho trượt giá ngẫu nhiên.
        spread_range (tuple): Khoảng (min, max) cho spread ngẫu nhiên.

    Returns:
        pd.Series: Chuỗi lợi nhuận của chiến lược sau khi đã trừ tất cả chi phí.
    """
    # 1. Tính toán hai đường MVWAP (Không đổi)
    mvwap_fast = df['tp_vol'].rolling(window=a).sum() / (df['volume'].rolling(window=a).sum() + 1e-9)
    mvwap_slow = df['tp_vol'].rolling(window=b).sum() / (df['volume'].rolling(window=b).sum() + 1e-9)

    # 2. Tạo tín hiệu Long/Short (-1 = Short, 1 = Long) (Không đổi)
    signal = np.sign(mvwap_fast - mvwap_slow)

    # 3. Tính toán lợi nhuận thị trường và dịch chuyển tín hiệu (Không đổi)
    market_returns = df['Close'].pct_change()
    shifted_signal = signal.shift(1).fillna(0)

    # 4. Tính lợi nhuận chiến lược thô (chưa có chi phí)
    strategy_returns = market_returns * shifted_signal

    # 5. TÍNH TOÁN VÀ ÁP DỤNG TẤT CẢ CÁC CHI PHÍ
    # Xác định các điểm có giao dịch (nơi tín hiệu đảo chiều)
    trades = shifted_signal.diff().ne(0)
    num_trades = trades.sum()

    # Nếu không có giao dịch nào, không cần làm gì thêm
    if num_trades == 0:
        return strategy_returns.fillna(0)

    # Tạo ra các chi phí ngẫu nhiên cho MỖI giao dịch
    random_slippage = np.random.uniform(slippage_range[0], slippage_range[1], num_trades)
    random_spread = np.random.uniform(spread_range[0], spread_range[1], num_trades)

    # Tổng chi phí tại mỗi điểm giao dịch
    total_transaction_costs = fee_rate + random_slippage + random_spread

    # Tạo một Series chứa tổng chi phí, chỉ có giá trị tại các điểm giao dịch
    costs_series = pd.Series(0.0, index=df.index)
    costs_series.loc[trades] = total_transaction_costs

    # Trừ đi tổng chi phí từ lợi nhuận thô để có lợi nhuận ròng
    strategy_returns_net = strategy_returns - costs_series

    return strategy_returns_net.fillna(0)

def sweep_vwap(df, a_range, b_range):
    """
    Quét qua các tham số khác nhau của chiến lược MVWAP crossover.

    Args:
        df (pd.DataFrame): DataFrame dữ liệu.
        a_range (range): Dải tham số cho MVWAP nhanh.
        b_range (range): Dải tham số cho MVWAP chậm.

    Returns:
        dict: Một dictionary với key là (a, b) và value là Sharpe Ratio.
    """
    metrics = {}

    # Sử dụng tqdm để tạo thanh tiến trình đẹp mắt
    for a in tqdm(a_range, desc="Quét MVWAP"):
        for b in b_range:
            # Đảm bảo a < b để logic giao cắt nhanh/chậm có ý nghĩa
            if a < b/1.2:
                # Chạy backtest cho cặp tham số (a,b)
                bt_returns = backtest_vwap(df, a, b)

                # Tính Sharpe Ratio
                metrics[(a, b)] = calculate_sharpe_ratio(bt_returns, data_frequency)

    return metrics

In [ ]:
# Tính giá điển hình (Typical Price) - hlc3
# Đây là "giá đại diện" cho mỗi cây nến, đúng như trong nghiên cứu
data['hlc3'] = (data['High'] + data['Low'] + data['Close']) / 3
# Tính giá trị giao dịch (Typical Price x Volume)
# Chuẩn bị sẵn tử số cho công thức VWAP
data['tp_vol'] = data['hlc3'] * data['volume']

# ======================================================================
# THỰC THI SWEEP TEST
# ======================================================================

# Định nghĩa dải tham số để quét

a_range = range(2, 144, 2)  # Dải chi tiết hơn
b_range = range(3, 987, 3)

# Chạy sweep test
met = sweep_vwap(data, a_range, b_range)

# Sắp xếp kết quả để xem 5 cặp tham số tốt nhất
sorted_met = sorted(met.items(), key=lambda item: item[1], reverse=True)

print("\n--- 10 cặp tham số MVWAP tốt nhất (dựa trên Sharpe Ratio) ---")
for params, sharpe in sorted_met[:10]:
    print(f"MVWAP Nhanh: {params[0]}, MVWAP Chậm: {params[1]} -> Sharpe Ratio (năm): {sharpe:.2f}")

Quét MVWAP:   0%|          | 0/71 [00:00<?, ?it/s]


--- 10 cặp tham số MVWAP tốt nhất (dựa trên Sharpe Ratio) ---
MVWAP Nhanh: 82, MVWAP Chậm: 687 -> Sharpe Ratio (năm): 3.09
MVWAP Nhanh: 82, MVWAP Chậm: 681 -> Sharpe Ratio (năm): 3.05
MVWAP Nhanh: 82, MVWAP Chậm: 678 -> Sharpe Ratio (năm): 2.86
MVWAP Nhanh: 82, MVWAP Chậm: 684 -> Sharpe Ratio (năm): 2.68
MVWAP Nhanh: 82, MVWAP Chậm: 690 -> Sharpe Ratio (năm): 2.68
MVWAP Nhanh: 122, MVWAP Chậm: 702 -> Sharpe Ratio (năm): 2.61
MVWAP Nhanh: 118, MVWAP Chậm: 699 -> Sharpe Ratio (năm): 2.58
MVWAP Nhanh: 94, MVWAP Chậm: 684 -> Sharpe Ratio (năm): 2.55
MVWAP Nhanh: 140, MVWAP Chậm: 717 -> Sharpe Ratio (năm): 2.55
MVWAP Nhanh: 84, MVWAP Chậm: 678 -> Sharpe Ratio (năm): 2.53


In [ ]:
# ======================================================================
# BƯỚC 0: AN TOÀN DỮ LIỆU (Giữ nguyên)
# ======================================================================
data['open_time'] = pd.to_datetime(data['open_time'])
data = data.sort_values(by='open_time')

# ======================================================================
# BƯỚC 1: LẤY TOP 5 CHIẾN LƯỢC VÀ CHUẨN BỊ DỮ LIỆU
# ======================================================================
sorted_met = sorted(met.items(), key=lambda item: item[1], reverse=True)
top_params = [item[0] for item in sorted_met[:10]]

results_to_plot = {}
for params in top_params:
    a, b = params
    returns = backtest_vwap(data, a, b)
    equity_curve = (1 + returns).cumprod()
    results_to_plot[params] = {'equity': equity_curve}

# ======================================================================
# BƯỚC 2: TÍNH TOÁN HIỆU SUẤT CỦA CHIẾN LƯỢC "BUY & HOLD"
# ======================================================================
# 2.1 Tính lợi nhuận theo từng kỳ của việc chỉ giữ BTC
buy_and_hold_returns = data['Close'].pct_change().fillna(0)

# 2.2 Tính đường cong vốn cho Buy & Hold
buy_and_hold_equity = (1 + buy_and_hold_returns).cumprod()

# ======================================================================
# BƯỚC 3: VẼ BIỂU ĐỒ SO SÁNH HIỆU SUẤT DUY NHẤT
# ======================================================================
# Khởi tạo một biểu đồ đơn
fig = go.Figure()

# 3.1 Vẽ các đường cong vốn của Top 5 chiến lược
for params, result_data in results_to_plot.items():
    fig.add_trace(
        go.Scatter(
            x=data['open_time'],
            y=result_data['equity'],
            mode='lines',
            name=f'Equity ({params[0]}, {params[1]})'
        )
    )

# 3.2 Vẽ đường cong vốn của chiến lược Buy & Hold để làm đường cơ sở
fig.add_trace(
    go.Scatter(
        x=data['open_time'],
        y=buy_and_hold_equity,
        mode='lines',
        name=f'Buy & Hold {ticker}',
        line=dict(color='black', width=2, dash='dash') # Làm cho nó nổi bật
    )
)

# 3.3 Cấu hình giao diện biểu đồ
fig.update_layout(
    title_text='So sánh Hiệu suất: Top 5 Chiến lược Giao cắt MVWAP vs. Buy & Hold',
    height=700,
    xaxis_title='Thời gian',
    yaxis_title='Vốn (chuẩn hóa)',
    legend_title_text='Chiến lược',
    hovermode='x unified',
    yaxis_type="log" # Sử dụng trục y log để so sánh tăng trưởng phần trăm tốt hơn
)

fig.show()